In [1]:
import json
import math

import numpy as np

import os
os.getcwd()
os.environ['KMP_DUPLICATE_LIB_OK'] = 'True'
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '0'


import tensorflow as tf
from keras.models import Sequential
from keras.layers import Dense, Flatten

Using TensorFlow backend.


In [2]:
def drawData (X,y,predictions=None):
    bu = "┌───┬───┬───┐"
    bm = "├───┼───┼───┤"
    bd = "└───┴───┴───┘"
    symbols = " XO*"
    for i, board in enumerate(X):
        for row in range(7):
            for column in range(2):
                if predictions is None and column == 1:
                    break
                if row == 0:
                    print(bu,end=" ")
                elif row == 6:
                    print(bd,end=" ")
                elif row % 2 == 0:
                    print(bm,end=" ")
                else:
                    for j in range(3):
                        k = int(j+3/2*(row-1))
                        if column == 0:
                            mark = " " + symbols[int(board[0][k]) + 2*int(board[1][k]) -int(y[i][k])] + " "
                        else:
                            mark = "{:.1f}".format(predictions[i][k])
                            if mark == "-0.0":
                                mark = "0.0"

                        print("│" + mark,end="")
                    print("│",end=" ")
            print("")

def drawBoard(match):
    bu = "┌───┬───┬───┬───┬───┐"
    bm = "├───┼───┼───┼───┼───┤"
    bd = "└───┴───┴───┴───┴───┘"
    for row in range(11):
        for i, turn in enumerate(match):
            # select the boards to be shown           
            if i != 0:
                if row == 0:
                    print(bu, end="   ")
                elif row == 10:
                    print(bd, end="   ")
                elif row % 2 == 0:
                    print(bm, end="   ")
                else:
                    for j in range(5):
                        mark = str(turn["board"][int(j+5/2*(row-1))])
                        if mark == "0":
                            mark = " "
                        elif mark == "1":
                            mark = "X"
                        elif mark == "2":
                            mark = "O"
                        elif mark == "-1":
                            mark = "*"
                        print("│ " + mark + " ", end="")
                    print("│   ", end="")
        print("")        

def drawBoardTight(match):    
    bu = "┌─┬─┬─┬─┬─┐"
    bm = "├─┼─┼─┼─┼─┤"
    bd = "└─┴─┴─┴─┴─┘"
    for row in range(11):
        for i, turn in enumerate(match):
            # select the boards to be shown           
            if i != 0:
                if row == 0:
                    print(bu, end=" ")
                elif row == 10:
                    print(bd, end=" ")
                elif row % 2 == 0:
                    print(bm, end=" ")
                else:
                    for j in range(5):
                        mark = str(turn["board"][int(j+5/2*(row-1))])
                        if mark == "0":
                            mark = " "
                        elif mark == "1":
                            mark = "X"
                        elif mark == "2":
                            mark = "O"
                        elif mark == "-1":
                            mark = "*"
                        print("│" + mark, end="")
                    print("│ ", end="")
        print("")   
        
def drawSimpBoard(predictions,roundto):      # draws predictions in a neat board 5*5
    for i, prediction in enumerate (predictions):
        output_prediction = prediction
        c = "{:" + str(roundto+3) + "." + str(roundto) +  "f}"
        if i % 5 == 0:
            print("\n" + " "*8, end="")
        print(c.format(output_prediction), end=" ")
    print("")

def transform (input_array):
    corners = [[1,3,9,7], [7,9,3,1]]
    edges = [[2,6,8,4], [8,6,2,4]]
    output_arrays = []
    for variant in range(2):
        for turn in range(4):
            new_array = [0,0,0,0,0,0,0,0,0]
            for position in range(1,10):
                for i in range(4):
                    if position == corners[variant][i]:
                        new_array[corners[0][(i+turn)%4]-1] = input_array[position-1]
                    elif position == edges[variant][i]:
                        new_array[edges[0][(i+turn)%4]-1] = input_array[position-1]
                    elif position == 5:
                        new_array[4] = input_array[position-1]
            output_arrays.append(new_array)
    return output_arrays

In [3]:
def read_training_data (filename): # returns JSON object as a dictionary
    datafile = open(filename)
    dataset = json.load(datafile)   
    return dataset

def X_y_training_data (dataset, layers=2, pixels=5*5):
    datasize = len(dataset)
    
    X = np.zeros([datasize, layers, pixels])
    y = np.zeros([datasize, pixels])
    
    for i, data_elem in enumerate(dataset):
        for p, pixel in enumerate(data_elem["board"]):
            if pixel == 1:
                X[i,0,p] = 1.0
            elif pixel == 2:
                X[i,1,p] = 1.0
        for r, rated_move in enumerate(data_elem["rated_moves"]):
            y[i,r] = rated_move
            
    return X, y

In [4]:
def initialize_model (input_layers=2, pixels=5*5, neurons=90):
    model = Sequential()
    model.add(Dense(pixels, input_shape=(input_layers,pixels), activation='relu',name="input"))
    model.add(Flatten(name="flatten"))
    model.add(Dense(neurons, activation='relu', name="h1"))
    model.add(Dense(neurons, activation='relu', name="h2"))
    model.add(Dense(neurons, activation='relu', name="h3"))
    model.add(Dense(pixels, name="output"))
    # model.summary ()        
    return model

def train_model (model, X, y, epochs=300, batch_size=30):    
    model.compile(loss='mean_absolute_error', optimizer='adam', metrics=['mse'])
    model.fit (X, y, epochs=epochs, batch_size=batch_size, verbose=0)

    mae, mse = model.evaluate(X, y, verbose=0)
    print('Mean squared error train: %.4f' % (mse))

In [5]:
def add_to_learned (learned_data, board, rated_moves):
    index = None
    for i, data_elem in enumerate(learned_data):
        if np.array_equal(data_elem["board"], board):
            index = i
            
    position = np.argmax (np.abs(rated_moves)) # np.nonzero(rated_moves)[0][0]    
    
    count = np.zeros(25)
    count[position] = 1
        
    if index != None:
        learned_data[index]["rated_moves"][position] *= learned_data[index]["count_rm"][position]
        learned_data[index]["rated_moves"][position] += rated_moves[position]
        learned_data[index]["count_rm"]   [position] += 1
        learned_data[index]["rated_moves"][position] /= learned_data[index]["count_rm"][position]
    else:
        learned_data = np.append(learned_data, [{"board": board, "rated_moves": rated_moves, "count_rm": count}])
        
    return learned_data

In [13]:
# TODO: Transformations

n_size = 50
m_size = 500 

players = [{},{}]

fields_outside = (0,1,2,3,4,5,9,10,14,15,19,20,21,22,23,24)
winning_sets = {(6,7,8),(11,12,13),(16,17,18),(6,11,16),(7,12,17),(8,13,18),(6,12,18),(8,12,16)}

outside_rating   = -3
double_rating    = -2 
good_move_rating = 100
not_fatal_move   = 1

treshold_count_to_use_data = 50


learned_data = np.array ([{"board":[0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0],"rated_moves":[0,0,0,0,0,0,1,1,1,0,0,1,1,1,0,0,1,1,1,0,0,0,0,0,0],"count_rm":[0,0,0,0,0,0,1,1,1,0,0,1,1,1,0,0,1,1,1,0,0,0,0,0,0]}]) 

for n in range(n_size):
    print ("\n\n\n\n\n—————————————————————————————————————————————————————\nRUN:",n,"\n") 

    X,y = X_y_training_data(learned_data)
    
    for i, player in enumerate(players):
        player ['model'] = initialize_model()
        train_model(player['model'], X, y)
 
    """
    if n == 0:
        dataset = read_training_data ('../01_data/Data_25F_01.json')
        X,y = X_y_training_data (dataset)
    else: 
        filtered_learned_data = []
        for element in learned_data:
            if np.sum(element["count_rm"]) > treshold_count_to_use_data: 
                filtered_learned_data.append(element)
        X,y = X_y_training_data (filtered_learned_data)
    """
    
    
    """
    if len (X) > 30:
        batch_size = 30
    else:
        batch_size = len (X)
    if len (X) > 0:
        for i, player in enumerate (players):
            train_model (player['model'], X, y, epochs=300, batch_size=batch_size)
    """
    
    mu = 0
    sigma = 0.5
    
    for m in range (m_size):
        print ("\n\n\n[ MATCH",m,"]\n")
        
        match = []
        board = np.zeros(25, dtype=int)

        done = False
        
        for turn in range(9):
            X_board = np.zeros ((2,25))
            for e, element in enumerate (board):
                if element != 0:
                     X_board[element-1][e] = 1.0
 
            p = turn % 2
            
            # deviations = np.random.normal(mu, sigma, 25)
            predictions = players[p]['model'].predict(np.array([X_board])) # Komma weggemaxt
            # chosen = np.argmax(predictions + deviations)
            alt = np.zeros(25)
            for i, prediction in enumerate(predictions[0]):
                alt[i]=np.random.normal(prediction,sigma)
            chosen = np.argmax(alt)

            print("\n    (" + str(turn) + ") raw_predict:")
            drawSimpBoard(predictions[0],3)
            print("\n        chosen:", chosen)
            
            match.append({"board":np.copy(board),"move":chosen})
            
            if board[chosen] == 0:
                board[chosen] = p+1
            else:
                board[chosen] = -1
            
            victory = False
            for x in winning_sets:
                v = True 
                for y in x:
                    if board[y] != p+1:
                        v = False
                if v:
                    victory = True
                    break
            
            # Fertig? 4 Abbruchbedingungen:
                # 1) Mark außerhalb des Spielfelds
                # 2) Mark auf schon belegtes Feld
                # 3) 3 in einer Reihe
                # 4) 9. Zug (Feld voll)
            
            # Outside
            if chosen in fields_outside:
                rated_moves = np.zeros(25)
                rated_moves[chosen] = outside_rating
                
                learned_data = add_to_learned (learned_data, np.copy(match[-1]["board"]), np.copy(rated_moves)) # wieso np.copy?
                
                print ("\n# Outside! (field " + str(chosen) + ")\n")
                done = True
            
            # Double
            elif board[chosen] == -1:
                rated_moves = np.zeros(25)
                rated_moves[chosen] = double_rating
                
                learned_data = add_to_learned (learned_data, np.copy(match[-1]["board"]), np.copy(rated_moves))
                
                print ("\n# Double! (field " + str(chosen) + ")\n")
                done = True
                
            # Victory       
            elif victory:
                for i, t in enumerate(match):
                    rated_moves = np.zeros(25) 
                    rated_moves[t["move"]] = (-1)**(i+p)*good_move_rating*(i+1)/len(match)               # FALSCH!!!!
                    
                    print("rated_moves:", np.around(rated_moves,3))
                    
                    learned_data = add_to_learned (learned_data, np.copy(t["board"]),np.copy(rated_moves))
                    
                print("\n# Gewinn! (field " + str(chosen) + ")", x, "\n")
                done = True
            
            # Full
            elif turn == 8:
                done = True
            
            
            
            if done:
                break
        
        match.append ({"board":np.copy(board),"move":-1})
        drawBoardTight(match)

print ("\n\n\n learned_data", learned_data)
print ("\n\n\n filtered_learned_data", filtered_learned_data)






—————————————————————————————————————————————————————
RUN: 0 

Mean squared error train: 0.1762
Mean squared error train: 0.1764



[ MATCH 0 ]


    (0) raw_predict:

         0.000  0.000  0.000  0.000  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.000  0.000  0.000  0.000 

        chosen: 13

    (1) raw_predict:

        -0.073 -0.014  0.015 -0.026  0.005 
        -0.052  0.276  0.269  0.265  0.066 
         0.015  0.311  0.231  0.281 -0.055 
        -0.021  0.308  0.221  0.276 -0.081 
         0.039  0.023  0.023 -0.010 -0.035 

        chosen: 17

    (2) raw_predict:

         0.044  0.002 -0.072 -0.080  0.079 
         0.017  0.279  0.276  0.290  0.054 
         0.026  0.249  0.351  0.239 -0.082 
        -0.025  0.331  0.280  0.370 -0.030 
         0.044  0.046 -0.010 -0.009  0.085 

        chosen: 24

# Outside! (field 24)

┌─┬─┬─┬─┬─┐ ┌─┬─┬─┬─┬─┐ ┌─┬─┬─┬─┬─┐ 


│ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ 
└─┴─┴─┴─┴─┘ └─┴─┴─┴─┴─┘ └─┴─┴─┴─┴─┘ 



[ MATCH 15 ]


    (0) raw_predict:

         0.000  0.000  0.000  0.000  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.000  0.000  0.000  0.000 

        chosen: 7

    (1) raw_predict:

        -0.040  0.007 -0.013  0.013 -0.002 
        -0.064  0.263  0.275  0.287  0.052 
        -0.009  0.292  0.207  0.280  0.004 
         0.002  0.315  0.228  0.266 -0.019 
         0.043  0.028  0.018 -0.022 -0.063 

        chosen: 18

    (2) raw_predict:

         0.029 -0.057 -0.076 -0.091  0.051 
         0.023  0.308  0.309  0.269  0.060 
         0.006  0.260  0.316  0.284 -0.050 
         0.010  0.291  0.288  0.359 -0.005 
        -0.040 -0.006  0.013  0.064  0.077 

        chosen: 11

    (3) raw_predict:

        -0.066  0.040 -0.028  0.017 -0.017 
        -0.132  0.305  0.196  0.304  0.113 
         0

│ │ │X│ │ │ │ │ │X│ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │O│ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │ │ │ 
└─┴─┴─┴─┴─┘ └─┴─┴─┴─┴─┘ 



[ MATCH 25 ]


    (0) raw_predict:

         0.000  0.000  0.000  0.000  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.000  0.000  0.000  0.000 

        chosen: 16

    (1) raw_predict:

        -0.107 -0.002  0.031 -0.070 -0.022 
        -0.066  0.237  0.256  0.270  0.066 
         0.025  0.311  0.169  0.261 -0.058 
        -0.043  0.311  0.208  0.247 -0.084 
         0.052 -0.009  0.037 -0.035 -0.078 

        chosen: 16

# Double! (field 16)

┌─┬─┬─┬─┬─┐ ┌─┬─┬─┬─┬─┐ 
│ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │X│ │ │ │ │ │*│ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │

├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │O│ │ │ │ │ │O│ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │X│ 
└─┴─┴─┴─┴─┘ └─┴─┴─┴─┴─┘ └─┴─┴─┴─┴─┘ 



[ MATCH 38 ]


    (0) raw_predict:

         0.000  0.000  0.000  0.000  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.000  0.000  0.000  0.000 

        chosen: 8

    (1) raw_predict:

        -0.025 -0.030  0.023 -0.015  0.007 
        -0.049  0.278  0.238  0.286  0.057 
         0.069  0.288  0.215  0.304 -0.058 
        -0.015  0.304  0.224  0.286 -0.052 
         0.044  0.008  0.030  0.012 -0.058 

        chosen: 6

    (2) raw_predict:

        -0.008 -0.040 -0.039 -0.066  0.011 
        -0.024  0.331  0.352  0.314 -0.020 
         0.009  0.243  0.339  0.261 -0.030 
         0.069  0.331  0.296  0.353 -0.031 
 

│ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │X│ │ │ │ │ │X│ │ │ │ │X│X│ │ │ │ │X│X│ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │O│ │ │ │ │ │O│ │ │ │ │ │O│ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │ │O│ │ │ │ │ 
└─┴─┴─┴─┴─┘ └─┴─┴─┴─┴─┘ └─┴─┴─┴─┴─┘ └─┴─┴─┴─┴─┘ 



[ MATCH 46 ]


    (0) raw_predict:

         0.000  0.000  0.000  0.000  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.300  0.300  0.300  0.000 
         0.000  0.000  0.000  0.000  0.000 

        chosen: 18

    (1) raw_predict:

        -0.033 -0.012  0.025 -0.041  0.009 
        -0.062  0.282  0.234  0.286  0.022 
         0.058  0.300  0.233  0.305 -0.026 
        -0.064  0.302  0.233  0.303 -0.034 
        -0.001  0.005  0.016  0

...


    (1) raw_predict:

        -0.000 -0.000  0.000  0.000 -0.000 
        -0.000 -0.000  0.000 -0.000 -0.000 
        -0.000 -0.000 -0.000  0.000  0.000 
        -0.000 -0.000 -0.000  0.000 -0.000 
         0.000 -0.000  0.000  0.000 -0.000 

        chosen: 23

# Outside! (field 23)

┌─┬─┬─┬─┬─┐ ┌─┬─┬─┬─┬─┐ 
│ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │X│ │ │ │ │ │X│ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │O│ │ 
└─┴─┴─┴─┴─┘ └─┴─┴─┴─┴─┘ 



[ MATCH 423 ]


    (0) raw_predict:

         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000 -0.000 -0.000 
         0.000 -0.000 -0.000  0.000  0.000 
         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000  0.000 -0.000 

        chosen: 5

# Outside! (field 5)

┌─┬─┬─┬─┬─┐ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│X│ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
└─┴─┴


┌─┬─┬─┬─┬─┐ ┌─┬─┬─┬─┬─┐ 
│ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │X│ │ │ │ │ │X│ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ ├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ │ │O│ │ │ │ 
└─┴─┴─┴─┴─┘ └─┴─┴─┴─┴─┘ 



[ MATCH 443 ]


    (0) raw_predict:

         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000 -0.000 -0.000 
         0.000 -0.000 -0.000  0.000  0.000 
         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000  0.000 -0.000 

        chosen: 2

# Outside! (field 2)

┌─┬─┬─┬─┬─┐ 
│ │ │X│ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
└─┴─┴─┴─┴─┘ 



[ MATCH 444 ]


    (0) raw_predict:

         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000 -0.000 -0.000 
         0.000 -0.000 -0.000  0.000  0.000 
         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000  0.000 -0.000 

        chosen: 

│ │ │ │ │ │ │ │ │ │ │ │ 
└─┴─┴─┴─┴─┘ └─┴─┴─┴─┴─┘ 



[ MATCH 462 ]


    (0) raw_predict:

         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000 -0.000 -0.000 
         0.000 -0.000 -0.000  0.000  0.000 
         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000  0.000 -0.000 

        chosen: 9

# Outside! (field 9)

┌─┬─┬─┬─┬─┐ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │X│ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
└─┴─┴─┴─┴─┘ 



[ MATCH 463 ]


    (0) raw_predict:

         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000 -0.000 -0.000 
         0.000 -0.000 -0.000  0.000  0.000 
         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000  0.000 -0.000 

        chosen: 24

# Outside! (field 24)

┌─┬─┬─┬─┬─┐ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │X│ 
└─┴─┴─┴─┴─┘ 



[ MATCH 464 ]


    (0) raw_predict:

         0.000 

│ │ │ │ │ │ 
└─┴─┴─┴─┴─┘ 



[ MATCH 480 ]


    (0) raw_predict:

         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000 -0.000 -0.000 
         0.000 -0.000 -0.000  0.000  0.000 
         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000  0.000 -0.000 

        chosen: 0

# Outside! (field 0)

┌─┬─┬─┬─┬─┐ 
│X│ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
└─┴─┴─┴─┴─┘ 



[ MATCH 481 ]


    (0) raw_predict:

         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000 -0.000 -0.000 
         0.000 -0.000 -0.000  0.000  0.000 
         0.000  0.000 -0.000  0.000 -0.000 
        -0.000 -0.000  0.000  0.000 -0.000 

        chosen: 22

# Outside! (field 22)

┌─┬─┬─┬─┬─┐ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │ │ │ │ 
├─┼─┼─┼─┼─┤ 
│ │ │X│ │ │ 
└─┴─┴─┴─┴─┘ 



[ MATCH 482 ]


    (0) raw_predict:

         0.000  0.000 -0.000  0.000 -0.

KeyboardInterrupt: 